In [1]:
import pandas as pd
import numpy as np
import json 
import requests
from io import StringIO
from azure.storage.blob import BlobServiceClient, BlobClient, ContainerClient 
import time

In [2]:
owner = "dolthub"
database = "us-housing-prices-v2"  # Put the database
branch = "main"


# Set the query to retrieve the data
query = '''SELECT COUNT(*) FROM sales'''
res = requests.get(
  'https://www.dolthub.com/api/v1alpha1/{}/{}/{}'.format(owner, database, branch),
  params={'q': query},
  )

response = res.json()
total_count = int(response['rows'][0]['COUNT(*)'])
print(total_count)

106642382


In [ ]:

# Define the increment value
increment = 1000

# Starting offset
offset = 0

# Placeholder for the base SQL query, with an OFFSET placeholder
base_query = "SELECT * FROM sales WHERE state = 'NY' LIMIT 1000 OFFSET {offset}"

while True:
    # Update the SQL query with the current offset
    updated_query = base_query.format(offset=offset)
    print(updated_query)  # (Example) Execute the query here or print it out

    # Make the API request
    res = requests.get('https://www.dolthub.com/api/v1alpha1/{}/{}/{}'.format(owner, database, branch), params={'q': updated_query})
    values = res.json()

    # Process the results
    if "rows" in values:
        result = values['rows']
        if not result:  # Check if the result is empty
            break
        print(result)
    else:
        break  # Exit the loop if no "rows" key in the response

    # Increment the offset for the next iteration
    offset += increment

# Print the completion message
print("All data has been processed.")

SELECT * FROM sales WHERE state = 'NY' LIMIT 1000 OFFSET 0
[{'state': 'NY', 'property_zip5': '11795', 'property_street_address': '# 1299 MADISON AVE,', 'property_city': 'ISLIP', 'property_county': 'SUFFOLK', 'property_id': '362.-3-93', 'sale_datetime': '2017-05-30 00:00:00', 'property_type': 'ONE FAMILY YEAR-ROUND RESIDENCE', 'sale_price': '10000', 'seller_1_name': 'JOHN V. COPPOLA', 'buyer_1_name': 'TA CONSULTANTS GROUP INC.', 'building_num_units': None, 'building_year_built': None, 'source_url': 'https://swcf.orpts.ny.gov/cfapps/salesWebProd/salesWeb/main.cfm?page=downloadCounty', 'book': '12914', 'page': '965', 'transfer_deed_type': None, 'property_township': None, 'property_lat': None, 'property_lon': None, 'sale_id': None, 'deed_date': '2017-06-02 00:00:00', 'building_num_stories': None, 'building_num_beds': None, 'building_num_baths': None, 'building_area_sqft': None, 'building_assessed_value': None, 'building_assessed_date': '1970-01-01 00:00:00', 'land_area_acres': '0', 'land_a

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



[{'state': 'NY', 'property_zip5': '11706', 'property_street_address': '0 SAXON AVENUE', 'property_city': 'ISLIP', 'property_county': 'SUFFOLK', 'property_id': '318.-2-92', 'sale_datetime': '2016-04-13 00:00:00', 'property_type': 'RESIDENTIAL VACANT LAND', 'sale_price': '0', 'seller_1_name': 'AVI SHARABANI', 'buyer_1_name': 'JONMOR GROUP LLC', 'building_num_units': None, 'building_year_built': None, 'source_url': 'https://swcf.orpts.ny.gov/cfapps/salesWebProd/salesWeb/main.cfm?page=downloadCounty', 'book': '12863', 'page': '304', 'transfer_deed_type': None, 'property_township': None, 'property_lat': None, 'property_lon': None, 'sale_id': None, 'deed_date': '2016-05-05 00:00:00', 'building_num_stories': None, 'building_num_beds': None, 'building_num_baths': None, 'building_area_sqft': None, 'building_assessed_value': None, 'building_assessed_date': '1970-01-01 00:00:00', 'land_area_acres': '0', 'land_area_sqft': None, 'land_assessed_value': None, 'seller_2_name': None, 'buyer_2_name': No

In [ ]:
# Print the configuration
connection_string = ['connectionString']
CONNECTION_STRING_AZURE_STORAGE = connection_string
CONTAINER_AZURE = 'housingsales'
blob_name = 'housingsales.csv'

#Convert DATAFRAME to csv
output= StringIO()
df.to_csv(output, index=False)
data = output.getvalue()
output.close()

# Create the BlobServiceClient object
blob_service_client = BlobServiceClient.from_connection_string(CONNECTION_STRING_AZURE_STORAGE)

# Get a blob client using the container name and blob name
blob_client = blob_service_client.get_blob_client(container=CONTAINER_AZURE, blob=blob_name)

# Upload the CSV data
blob_client.upload_blob(data, overwrite=True)

print(f"Uploaded {blob_name} to Azure Blob Storage in container {CONTAINER_AZURE}.")